![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Systemy Dialogowe </h1>
<h2> 8. <i>Parsing semantyczny z wykorzystaniem technik uczenia maszynowego</i>  [laboratoria]</h2> 
<h3> Marek Kubis (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Parsing semantyczny z wykorzystaniem technik uczenia maszynowego
================================================================

Wprowadzenie
------------
Problem wykrywania slotów i ich wartości w wypowiedziach użytkownika można sformułować jako zadanie
polegające na przewidywaniu dla poszczególnych słów etykiet wskazujących na to czy i do jakiego
slotu dane słowo należy.

> chciałbym zarezerwować stolik na jutro**/day** na godzinę dwunastą**/hour** czterdzieści**/hour** pięć**/hour** na pięć**/size** osób

Granice slotów oznacza się korzystając z wybranego schematu etykietowania.

### Schemat IOB

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |

> chciałbym zarezerwować stolik na jutro**/B-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/I-hour** na pięć**/B-size** osób

### Schemat IOBES

| Prefix | Znaczenie                  |
|:------:|:---------------------------|
| I      | wnętrze slotu (inside)     |
| O      | poza slotem (outside)      |
| B      | początek slotu (beginning) |
| E      | koniec slotu (ending)      |
| S      | pojedyncze słowo (single)  |

> chciałbym zarezerwować stolik na jutro**/S-day** na godzinę dwunastą**/B-hour** czterdzieści**/I-hour** pięć**/E-hour** na pięć**/S-size** osób

Jeżeli dla tak sformułowanego zadania przygotujemy zbiór danych
złożony z wypowiedzi użytkownika z oznaczonymi slotami (tzw. *zbiór uczący*),
to możemy zastosować techniki (nadzorowanego) uczenia maszynowego w celu zbudowania modelu
annotującego wypowiedzi użytkownika etykietami slotów.

Do zbudowania takiego modelu można wykorzystać między innymi:

 1. warunkowe pola losowe (Lafferty i in.; 2001),

 2. rekurencyjne sieci neuronowe, np. sieci LSTM (Hochreiter i Schmidhuber; 1997),

 3. transformery (Vaswani i in., 2017).

Przykład
--------
Skorzystamy ze zbioru danych przygotowanego przez Schustera (2019).

In [32]:
!mkdir -p l07
%cd l07
!curl -L -C -  https://fb.me/multilingual_task_oriented_data  -o data.zip
!unzip data.zip
%cd ..

c:\Develop\wmi\AITECH\sem1\Systemy dialogowe\lab\l07


A subdirectory or file -p already exists.
Error occurred while processing: -p.
A subdirectory or file l07 already exists.
Error occurred while processing: l07.
** Resuming transfer from byte position 8923190
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed

  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0
  0     0    0     0    0     0      0      0 --:--:-- --:--:-- --:--:--     0

100    49  100    49    0     0    118      0 --:--:-- --:--:-- --:--:--   118


c:\Develop\wmi\AITECH\sem1\Systemy dialogowe\lab


'unzip' is not recognized as an internal or external command,
operable program or batch file.


Zbiór ten gromadzi wypowiedzi w trzech językach opisane slotami dla dwunastu ram należących do trzech dziedzin `Alarm`, `Reminder` oraz `Weather`. Dane wczytamy korzystając z biblioteki [conllu](https://pypi.org/project/conllu/).

In [76]:
from conllu import parse_incr
fields = ['id', 'form', 'frame', 'slot']

def nolabel2o(line, i):
    return 'O' if line[i] == 'NoLabel' else line[i]
# pathTrain = '../tasks/zad8/en/train-en.conllu'
# pathTest = '../tasks/zad8/en/test-en.conllu'

pathTrain = '../tasks/zad8/pl/train.conllu'
pathTest = '../tasks/zad8/pl/test.conllu'

with open(pathTrain, encoding="UTF-8") as trainfile:
    i=0
    for line in trainfile:
        print(line)
        i+=1
        if i==15: break 
    trainset = list(parse_incr(trainfile, fields=fields, field_parsers={'slot': nolabel2o}))
with open(pathTest,  encoding="UTF-8") as testfile:
    testset = list(parse_incr(testfile, fields=fields, field_parsers={'slot': nolabel2o}))
    

# text: halo

# intent: hello

# slots: 

1	halo	hello	NoLabel



# text: chaciałbym pójść na premierę filmu jakie premiery są w tym tygodniu

# intent: reqmore

# slots: 

1	chaciałbym	reqmore	NoLabel

2	pójść	reqmore	NoLabel

3	na	reqmore	NoLabel

4	premierę	reqmore	NoLabel

5	filmu	reqmore	NoLabel

6	jakie	reqmore	NoLabel

7	premiery	reqmore	NoLabel



Zobaczmy kilka przykładowych wypowiedzi z tego zbioru.

In [34]:
from tabulate import tabulate
tabulate(trainset[1], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>wybieram</td><td>inform</td><td>O      </td></tr>\n<tr><td style="text-align: right;">2</td><td>batmana </td><td>inform</td><td>B-title</td></tr>\n</tbody>\n</table>'

In [77]:
tabulate(trainset[16], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chcę        </td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">2</td><td>zarezerwować</td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">3</td><td>bilety      </td><td>inform</td><td>O</td></tr>\n</tbody>\n</table>'

In [78]:
tabulate(trainset[20], tablefmt='html')

'<table>\n<tbody>\n<tr><td style="text-align: right;">1</td><td>chciałbym </td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">2</td><td>anulować  </td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">3</td><td>rezerwację</td><td>inform</td><td>O</td></tr>\n<tr><td style="text-align: right;">4</td><td>biletu    </td><td>inform</td><td>O</td></tr>\n</tbody>\n</table>'

Budując model skorzystamy z architektury opartej o rekurencyjne sieci neuronowe
zaimplementowanej w bibliotece [flair](https://github.com/flairNLP/flair) (Akbik i in. 2018).

In [38]:
from flair.data import Corpus, Sentence, Token
from flair.datasets import SentenceDataset
from flair.embeddings import StackedEmbeddings
from flair.embeddings import WordEmbeddings
from flair.embeddings import CharacterEmbeddings
from flair.embeddings import FlairEmbeddings
from flair.models import SequenceTagger
from flair.trainers import ModelTrainer

# determinizacja obliczeń
import random
import torch
random.seed(42)
torch.manual_seed(42)

if torch.cuda.is_available():
    torch.cuda.manual_seed(0)
    torch.cuda.manual_seed_all(0)
    torch.backends.cudnn.enabled = False
    torch.backends.cudnn.benchmark = False
    torch.backends.cudnn.deterministic = True

Dane skonwertujemy do formatu wykorzystywanego przez `flair`, korzystając z następującej funkcji.

In [39]:
def conllu2flair(sentences, label=None):
    fsentences = []

    for sentence in sentences:
        fsentence = Sentence()

        for token in sentence:
            ftoken = Token(token['form'])

            if label:
                ftoken.add_tag(label, token[label])

            fsentence.add_token(ftoken)

        fsentences.append(fsentence)

    return SentenceDataset(fsentences)

corpus = Corpus(train=conllu2flair(trainset, 'slot'), test=conllu2flair(testset, 'slot'))
print(corpus)
tag_dictionary = corpus.make_tag_dictionary(tag_type='slot')
print(tag_dictionary)

Corpus: 297 train + 33 dev + 33 test sentences
Dictionary with 14 tags: <unk>, O, B-date, I-date, B-time, I-time, B-area, I-area, B-title, B-quantity, I-title, I-quantity, <START>, <STOP>


Nasz model będzie wykorzystywał wektorowe reprezentacje słów (zob. [Word Embeddings](https://github.com/flairNLP/flair/blob/master/resources/docs/TUTORIAL_3_WORD_EMBEDDING.md)).

In [40]:
embedding_types = [
    WordEmbeddings('pl'),
    FlairEmbeddings('polish-forward'),
    FlairEmbeddings('polish-backward'),
    CharacterEmbeddings(),
]

embeddings = StackedEmbeddings(embeddings=embedding_types)
tagger = SequenceTagger(hidden_size=256, embeddings=embeddings,
                        tag_dictionary=tag_dictionary,
                        tag_type='slot', use_crf=True)

2022-04-28 22:14:01,525 https://flair.informatik.hu-berlin.de/resources/embeddings/token/pl-wiki-fasttext-300d-1M.vectors.npy not found in cache, downloading to C:\Users\48516\AppData\Local\Temp\tmp8ekygs88


100%|██████████| 1199998928/1199998928 [01:00<00:00, 19734932.13B/s]

2022-04-28 22:15:02,505 copying C:\Users\48516\AppData\Local\Temp\tmp8ekygs88 to cache at C:\Users\48516\.flair\embeddings\pl-wiki-fasttext-300d-1M.vectors.npy


2022-04-28 22:15:03,136 removing temp file C:\Users\48516\AppData\Local\Temp\tmp8ekygs88
2022-04-28 22:15:03,420 https://flair.informatik.hu-berlin.de/resources/embeddings/token/pl-wiki-fasttext-300d-1M not found in cache, downloading to C:\Users\48516\AppData\Local\Temp\tmp612sxdgl


100%|██████████| 40874795/40874795 [00:02<00:00, 18943852.55B/s]

...

2022-04-28 22:15:17,599 copying C:\Users\48516\AppData\Local\Temp\tmp05k_xff8 to cache at C:\Users\48516\.flair\embeddings\lm-polish-forward-v0.2.pt
2022-04-28 22:15:17,640 removing temp file C:\Users\48516\AppData\Local\Temp\tmp05k_xff8


2022-04-28 22:15:18,034 https://flair.informatik.hu-berlin.de/resources/embeddings/flair/lm-polish-backward-v0.2.pt not found in cache, downloading to C:\Users\48516\AppData\Local\Temp\tmpbjevekqx


100%|██████████| 84244196/84244196 [00:04<00:00, 19850177.72B/s]

2022-04-28 22:15:22,467 copying C:\Users\48516\AppData\Local\Temp\tmpbjevekqx to cache at C:\Users\48516\.flair\embeddings\lm-polish-backward-v0.2.pt


2022-04-28 22:15:22,518 removing temp file C:\Users\48516\AppData\Local\Temp\tmpbjevekqx


Zobaczmy jak wygląda architektura sieci neuronowej, która będzie odpowiedzialna za przewidywanie
slotów w wypowiedziach.

In [41]:
print(tagger)

SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dropout): LockedDropout(p=0.5)
  (embedding2nn): Linear(in_features=4446, out_features=4446, bias=True)
  (rnn): LSTM(4446, 256, batch_first=True, bidirectiona

Wykonamy dziesięć iteracji (epok) uczenia a wynikowy model zapiszemy w katalogu `slot-model`.

In [42]:
trainer = ModelTrainer(tagger, corpus)
trainer.train('slot-model',
              learning_rate=0.1,
              mini_batch_size=32,
              max_epochs=10,
              train_with_dev=False)

2022-04-28 22:15:23,085 ----------------------------------------------------------------------------------------------------
2022-04-28 22:15:23,086 Model: "SequenceTagger(
  (embeddings): StackedEmbeddings(
    (list_embedding_0): WordEmbeddings('pl')
    (list_embedding_1): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_2): FlairEmbeddings(
      (lm): LanguageModel(
        (drop): Dropout(p=0.25, inplace=False)
        (encoder): Embedding(1602, 100)
        (rnn): LSTM(100, 2048)
        (decoder): Linear(in_features=2048, out_features=1602, bias=True)
      )
    )
    (list_embedding_3): CharacterEmbeddings(
      (char_embedding): Embedding(275, 25)
      (char_rnn): LSTM(25, 25, bidirectional=True)
    )
  )
  (word_dropout): WordDropout(p=0.05)
  (locked_dr

{'test_score': 0.5294117647058824,
 'dev_score_history': [0.0,
  0.0,
  0.0,
  0.0,
  0.2222222222222222,
  0.3333333333333333,
  0.5,
  0.5,
  0.7142857142857143,
  0.7142857142857143],
 'train_loss_history': [5.108907747268677,
  2.6376620531082153,
  2.0286046147346495,
  1.816417047381401,
  1.7658178985118866,
  1.5524149179458617,
  1.384124332666397,
  1.3110598623752594,
  1.0780560612678527,
  0.8734622806310653],
 'dev_loss_history': [1.1116931438446045,
  1.2027416229248047,
  0.9265440702438354,
  0.8311207890510559,
  0.7797471880912781,
  0.9345423579216003,
  0.6798948049545288,
  0.5563207864761353,
  0.909138560295105,
  0.5443210601806641]}

Jakość wyuczonego modelu możemy ocenić, korzystając z zaraportowanych powyżej metryk, tj.:

 - *tp (true positives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fp (false positives)*

   > liczba słów nieoznaczonych w zbiorze testowym etykietą $e$, które model oznaczył tą etykietą

 - *fn (false negatives)*

   > liczba słów oznaczonych w zbiorze testowym etykietą $e$, którym model nie nadał etykiety $e$

 - *precision*

   > $$\frac{tp}{tp + fp}$$

 - *recall*

   > $$\frac{tp}{tp + fn}$$

 - $F_1$

   > $$\frac{2 \cdot precision \cdot recall}{precision + recall}$$

 - *micro* $F_1$

   > $F_1$ w którym $tp$, $fp$ i $fn$ są liczone łącznie dla wszystkich etykiet, tj. $tp = \sum_{e}{{tp}_e}$, $fn = \sum_{e}{{fn}_e}$, $fp = \sum_{e}{{fp}_e}$

 - *macro* $F_1$

   > średnia arytmetyczna z $F_1$ obliczonych dla poszczególnych etykiet z osobna.

Wyuczony model możemy wczytać z pliku korzystając z metody `load`.

In [43]:
model = SequenceTagger.load('slot-model/final-model.pt')

2022-04-28 22:17:33,278 loading file slot-model/final-model.pt


Wczytany model możemy wykorzystać do przewidywania slotów w wypowiedziach użytkownika, korzystając
z przedstawionej poniżej funkcji `predict`.

In [44]:
def predict(model, sentence):
    csentence = [{'form': word} for word in sentence]
    fsentence = conllu2flair([csentence])[0]
    model.predict(fsentence)
    return [(token, ftoken.get_tag('slot').value) for token, ftoken in zip(sentence, fsentence)]


Jak pokazuje przykład poniżej model wyuczony tylko na 100 przykładach popełnia w dosyć prostej
wypowiedzi błąd etykietując słowo `alarm` tagiem `B-weather/noun`.

In [90]:
tabulate(predict(model, 'batman'.split()), tablefmt='html')

'<table>\n<tbody>\n<tr><td>co        </td><td>O</td></tr>\n<tr><td>gracie    </td><td>O</td></tr>\n<tr><td>popołudniu</td><td>O</td></tr>\n</tbody>\n</table>'

Literatura
----------
 1. Sebastian Schuster, Sonal Gupta, Rushin Shah, Mike Lewis, Cross-lingual Transfer Learning for Multilingual Task Oriented Dialog. NAACL-HLT (1) 2019, pp. 3795-3805
 2. John D. Lafferty, Andrew McCallum, and Fernando C. N. Pereira. 2001. Conditional Random Fields: Probabilistic Models for Segmenting and Labeling Sequence Data. In Proceedings of the Eighteenth International Conference on Machine Learning (ICML '01). Morgan Kaufmann Publishers Inc., San Francisco, CA, USA, 282–289, https://repository.upenn.edu/cgi/viewcontent.cgi?article=1162&context=cis_papers
 3. Sepp Hochreiter and Jürgen Schmidhuber. 1997. Long Short-Term Memory. Neural Comput. 9, 8 (November 15, 1997), 1735–1780, https://doi.org/10.1162/neco.1997.9.8.1735
 4. Ashish Vaswani, Noam Shazeer, Niki Parmar, Jakob Uszkoreit, Llion Jones, Aidan N. Gomez, Lukasz Kaiser, Illia Polosukhin, Attention is All you Need, NIPS 2017, pp. 5998-6008, https://arxiv.org/abs/1706.03762
 5. Alan Akbik, Duncan Blythe, Roland Vollgraf, Contextual String Embeddings for Sequence Labeling, Proceedings of the 27th International Conference on Computational Linguistics, pp. 1638–1649, https://www.aclweb.org/anthology/C18-1139.pdf
